In [ ]:
import json
import pandas as pd
import numpy as np
import spacy
from tqdm import tqdm
import pickle

: 

In [2]:
import os
os.environ["HF_HOME"] = "/data/btp_data/Siddharth/huggingface_cache/"

In [3]:
from sentence_transformers import SentenceTransformer

In [5]:
encoder = SentenceTransformer('all-mpnet-base-v2')

README.md:   0%|          | 0.00/10.6k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/438M [00:00<?, ?B/s]

In [9]:
nlp = spacy.load("en_core_web_sm")
encodings = {}

In [8]:
for js in tqdm(list(os.listdir("Parsed_pds"))[:]):
    js_file = json.loads(open("Parsed_pds/%s"%js,"r").read())
    body_text = js_file['pdf_parse']['body_text']
    text = [x['text'] for x in body_text]
    if len(js_file['pdf_parse']['abstract'])>0:
        text.insert(0,js_file['pdf_parse']['abstract'][0]['text'])
    text = " ".join(text)
    doc = nlp(text)
    sentences = [x for x in doc.sents if len(x)>5]
    
    enc = encoder.encode(sentences)
    encodings[js[:-5]] = {}
    for idx in range(0,len(enc)):
        encodings[js[:-5]][str(sentences[idx])] = enc[idx]

  1%|          | 59/8486 [00:37<1:28:07,  1.59it/s]


KeyboardInterrupt: 

In [10]:
pos_claims = json.loads(open("positive_claims_extracted.json","r").read())
for fileno in tqdm(list(pos_claims.keys())[:]):
    js_file = json.loads(open("Parsed_pds/%s.json"%fileno,"r").read())
    body_text = js_file['pdf_parse']['body_text']
    text = [x['text'] for x in body_text]
    if len(js_file['pdf_parse']['abstract'])>0:
        text.insert(0,js_file['pdf_parse']['abstract'][0]['text'])
    text = " ".join(text)
    doc = nlp(text)
    sentences = [x for x in doc.sents if len(x)>5]
    
    enc = encoder.encode(sentences)
    encodings[fileno] = {}
    for idx in range(0,len(enc)):
        encodings[fileno][str(sentences[idx])] = enc[idx]

100%|██████████| 1000/1000 [10:56<00:00,  1.52it/s]


In [31]:
neg_claims = json.loads(open('negative_claims_generated.json',"r").read())

In [42]:
def extract_negated_claims(output):
    # Split the output by newline
    output_lines = [x for x in output.split('\n') if len(x.strip())>0]

    negated_claims = []

    # Check if every split output after the first has a colon
    # if all(':' in line for line in output_lines[1:]):
    #     # If the first line just says "Claim:", ignore it
    #     if output_lines[0].strip().lower() == "claim:":
    #         negated_claims.extend(output_lines[1:])
    #     else:
    #         negated_claims.extend(output_lines)
    
    # Check if there are split outputs that start with a star or bullet points
    if any(line.strip().startswith(('*', '•', '-', '–', '1.', '2.', '3.', '4.', '5.', '6.', '7.', '8.', '9.', '10.')) for line in output_lines):
        for line in output_lines:
            if line.strip().startswith(('*', '•', '-', '–', '1.', '2.', '3.', '4.', '5.', '6.', '7.', '8.', '9.', '10.')):
                negated_claims.append(line.strip('•–*-12345678910.').strip())
    
    # If every split output has a "Claim:", use all of them as negated outputs
    # elif all(line.strip().lower().startswith("claim:") for line in output_lines):
    #     negated_claims.extend(output_lines)
    
    # elif all(line.strip().lower().startswith("claim:") for line in output_lines[1:]):
    #     negated_claims.extend(output_lines[1:])


    return negated_claims

In [46]:
c=0
t= 0
for file in neg_claims:
    for pos_claim in neg_claims[file]:
        neg_claims_cur = neg_claims[file][pos_claim]
        for negated_claim in neg_claims_cur:
            t+=1
            if len(extract_negated_claims(negated_claim))==0:
                c+=1
                print(negated_claim)
            else:
                pass
                # print(negated_claim)
                # print(extract_negated_claims(negated_claim))       
            print("\n-----------------\n")


-----------------

  Sure! Here are the negated claims based on the given claim:

Claim:
The two reduction methods of PCA and t-SNE represent a popular classical technique and a recently proposed technique that underperforms other recent competitors (LLE, Isomap, MVU, CCA, Laplacian eigenmaps).

-----------------


-----------------


-----------------


-----------------


-----------------

  Sure, I'd be happy to help! Here are some negated versions of the given claim:

Claim: The adaptive Ad-aBERT can find different models varying in model efficiencies and architectures that are suitable for different downstream tasks.

Negated Claim: The adaptive Ad-aBERT is limited to finding models with fixed efficiencies and architectures that are only suitable for a specific set of downstream tasks, rather than being adaptable to a wide range of tasks.

-----------------


-----------------


-----------------


-----------------


-----------------


-----------------


-----------------


-

In [45]:
print(c,t)

4819 19170


In [ ]:

with open('pdf_encoded.pickle', 'wb') as f:
    pickle.dump(encodings, f)

In [11]:
T5_prompt = "verify: %s <sep> evidence: %s <sep>"

In [12]:
def isConclusion(section):
    
    if "conclusion" in section.lower() or "discussion" in section.lower():
        return True
    return False

In [13]:
with open("pdf_encoded.pickle","rb") as f:
    encodings_dict = pickle.load(f)

In [14]:
def get_encodings(doc_no,sentences):
    enc = []
    for sentence in sentences:
        try:
            enc.append(encodings_dict[doc_no][sentence])
        except KeyError:
            enc.append(encoder.encode(sentence))
    return enc

In [15]:
from sklearn.metrics.pairwise import cosine_similarity

def get_evidence(claim_encoding,evidence_encodings,top_n,evidences):
    similarities = cosine_similarity(claim_encoding.reshape(1, -1), evidence_encodings)[0]
    
    # Get indices of top N similar embeddings
    top_indices = np.argsort(similarities)[::-1][:top_n]
    
    # Get top N similar embeddings and their cosine similarity scores
    top_embeddings = [evidence_encodings[i] for i in top_indices]
    top_scores = [similarities[i] for i in top_indices]
    top_evidences = [evidences[i] for i in top_indices]

    return " ".join(top_evidences)

In [16]:
pos_claims = json.loads(open("positive_claims_extracted.json","r").read())
dataset = []
for fileno in tqdm(list(pos_claims.keys())[:1000]):
    js_file = json.loads(open("Parsed_pds/%s.json"%fileno,"r").read())
    body_text = js_file['pdf_parse']['body_text']
    text = [x['text'] for x in body_text if not isConclusion(x['section'])]
    if len(js_file['pdf_parse']['abstract'])>0:
        text.insert(0,js_file['pdf_parse']['abstract'][0]['text'])
    text = " ".join(text)
    doc = nlp(text)
    sentences = [str(x) for x in doc.sents if len(x)>5]
    
    enc = get_encodings(fileno,sentences)
    claim_enc = encoder.encode(pos_claims[fileno])

    for idx,claim in enumerate(pos_claims[fileno]):
        ev = get_evidence(claim_enc[idx],enc,10,sentences)
        dataset.append([fileno,claim,ev])
    

  0%|          | 0/1000 [00:00<?, ?it/s]

100%|██████████| 1000/1000 [09:34<00:00,  1.74it/s]


In [17]:
dataset = pd.DataFrame(dataset)

In [18]:
from transformers import pipeline

pipe = pipeline("text2text-generation", model="google-t5/t5-base")

In [19]:
claim = "The earth is flat."

# Example evidence
evidence = "Scientific consensus supports the round-earth model."

# Format the input prompt
prompt = f"verify claim: %s <sep> evidence: %s <sep>"

# Generate the response
response = pipe(prompt, max_length=128, num_return_sequences=1)

# Extract the response text
response_text = response[0]['generated_text']

print("Response:", response_text)

Response: True


In [20]:
responses =
for row in dataset.itertuples():
    prompt = f"verify claim: %s <sep> evidence: %s <sep>"

    # Generate the response
    response = pipe(prompt%(row[2],row[3]), max_length=128, num_return_sequences=1)

    # Extract the response text
    response_text = response[0]['generated_text']

    print("Response:", response_text)

Response: True
Response: True
Response: True
Response: True
Response: True
Response: True
Response: True
Response: True
Response: True
Response: True
Response: True
Response: False
Response: True
Response: False
Response: False
Response: True
Response: False
Response: True
Response: True
Response: True
Response: True
Response: True
Response: True
Response: True
Response: True
Response: True
Response: True
Response: True
Response: True
Response: True
Response: True
Response: True
Response: False
Response: True
Response: True
Response: True
Response: True
Response: True
Response: True
Response: True
Response: True
Response: True
Response: True
Response: True
Response: True
Response: False
Response: True
Response: True
Response: True
Response: True
Response: True
Response: True
Response: True
Response: our proposed recurrent chunking mechanisms outperform benchmark models . default distributions P BKG (B), P F-INIT (F ), P E-INIT (E) . each cluster comprises 20 documents on a specific top

KeyboardInterrupt: 